In [1]:
import pandas as pd
import numpy as np
import nltk

from sklearn.model_selection import cross_val_score

from sklearn.metrics import f1_score
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report


from sklearn.linear_model import SGDClassifier

In [2]:
peoplesdaily = "/home/user/Desktop/china_document_level/corpus/Document/Peoples_Daily/20190128-Peoples_Daily_800_agreed.json"
rcv = "/home/user/Desktop/china_document_level/corpus/Document/RCV1_Code_China/20190221_Reuters_codeChina_SVM_RF_Bert_preds_Adjudication_base.json"
scmp = "/home/user/Desktop/china_document_level/corpus/Document/Scmp/20190321_scmp_AgreedByAll.xlsx"
scmp_random = "/home/user/Desktop/china_document_level/corpus/Document/Scmp_Random/20181225_scmp_25k_random-Merged_AgreedByAll.json"

peoplesdaily_df = pd.read_json(peoplesdaily, lines=True)
rcv_df = pd.read_json(rcv, lines=True)
scmp_df = pd.read_excel(scmp)
scmp_random_df = pd.read_json(scmp_random, lines=True )

#df = pd.read_json(file, lines=True)

In [3]:
scmp_random_df.head(5)

label                                               text  \
0      0  PUBLISHED : Saturday, 14 April, 2001, 12:00am\...   
1      0  Schools introducing continuous assessment for ...   
2      0  PUBLISHED : Monday, 27 December, 1999, 12:00am...   
3      0  Hubei tackles woes of farmers\nPUBLISHED : Mon...   
4      0  Patients give their eye teeth to see again\nPU...   

                                                 url  
0  http://www.scmp.com/article/344157/recognising...  
1  http://www.scmp.com/article/266444/schools-int...  
2  http://www.scmp.com/article/303874/airport-mil...  
3  http://www.scmp.com/article/378817/hubei-tackl...  
4  http://www.scmp.com/article/546584/patients-gi...

In [4]:
peoplesdaily_df = peoplesdaily_df[['text','label']]
rcv_df = rcv_df[['text','label']]
scmp_df = scmp_df[['text','label']]
scmp_random_df = scmp_random_df[['text', 'label']]


In [5]:
rcv_df.loc[rcv_df.label == 2, 'label'] = 0
scmp_random_df.loc[scmp_random_df.label == 2, 'label'] = 0

In [6]:
scmp_df = scmp_df.loc[~np.isnan(scmp_df['label'])]

In [7]:
#df = peoplesdaily_df.append(rcv_df, ignore_index=True)

In [8]:
df = peoplesdaily_df.append(scmp_df, ignore_index=True)

In [9]:
df = df.append(scmp_random_df, ignore_index=True)

In [10]:
df = df.rename(columns={'text': 'sentence'})

In [11]:
"""df.sentence = df.sentence.str.replace('\d+', '')
df_sent = (df['sentence'].str.len() > 10)
ne_df = df.loc[df_sent]
df = ne_df
df = df[~df.sentence.str.startswith('https')]
df = df[~df.sentence.str.startswith('url : ')]

"""

"df.sentence = df.sentence.str.replace('\\d+', '')\ndf_sent = (df['sentence'].str.len() > 10)\nne_df = df.loc[df_sent]\ndf = ne_df\ndf = df[~df.sentence.str.startswith('https')]\ndf = df[~df.sentence.str.startswith('url : ')]\n\n"

In [12]:
"""import nltk

w_tokenizer = nltk.tokenize.WhitespaceTokenizer()
lemmatizer = nltk.stem.WordNetLemmatizer()"""

'import nltk\n\nw_tokenizer = nltk.tokenize.WhitespaceTokenizer()\nlemmatizer = nltk.stem.WordNetLemmatizer()'

In [13]:
"""def lemmatize_text(text):
    return [lemmatizer.lemmatize(w) for w in w_tokenizer.tokenize(text)]

df.sentence = df.sentence.apply(lemmatize_text)"""

'def lemmatize_text(text):\n    return [lemmatizer.lemmatize(w) for w in w_tokenizer.tokenize(text)]\n\ndf.sentence = df.sentence.apply(lemmatize_text)'

In [14]:
df_X = df['sentence']
df_Y = df['label']

df_fina = pd.concat([df_X, df_Y], axis=1, sort=False)

In [34]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(df_X, df_Y, test_size=0.50, random_state=24)

In [35]:
def dummy_fun(doc):
    return doc

In [36]:
from sklearn.feature_extraction.text import TfidfVectorizer
tfidf_vect = TfidfVectorizer(stop_words='english', ngram_range=(1,2), tokenizer=dummy_fun, preprocessor=dummy_fun, analyzer='word', token_pattern=r'\w{1,}', max_features=20000)
train_tfidf = tfidf_vect.fit_transform(X_train)
test_tfidf = tfidf_vect.transform(X_test)

In [37]:
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVR
from sklearn import svm

gsc = GridSearchCV(
        estimator=svm.LinearSVC(),
        param_grid={
            'C': [0.1, 1, 10, 100, 1000]
        },
        cv=5, scoring='recall', verbose=1, n_jobs=-1)

In [38]:
grid_result = gsc.fit(train_tfidf, y_train)

best_params = grid_result.best_params_

Fitting 5 folds for each of 5 candidates, totalling 25 fits


[Parallel(n_jobs=-1)]: Done  18 out of  25 | elapsed:    4.6s remaining:    1.8s
[Parallel(n_jobs=-1)]: Done  25 out of  25 | elapsed:    6.9s finished


In [39]:
best_params

{'C': 1000}

In [40]:
best_svr = svm.LinearSVC(C=best_params["C"])
best_svr.fit(train_tfidf, y_train)

LinearSVC(C=1000, class_weight=None, dual=True, fit_intercept=True,
     intercept_scaling=1, loss='squared_hinge', max_iter=1000,
     multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
     verbose=0)

In [41]:
svm_predicted = best_svr.predict(test_tfidf)

In [42]:
"""from sklearn import svm
clf = svm.LinearSVC(penalty='l2', dual=False)
clf.fit(train_tfidf, y_train)
predicted = clf.predict(test_tfidf)"""

"from sklearn import svm\nclf = svm.LinearSVC(penalty='l2', dual=False)\nclf.fit(train_tfidf, y_train)\npredicted = clf.predict(test_tfidf)"

In [43]:
from sklearn.metrics import f1_score
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
print("SVM F1 Score : ")
print(f1_score(y_test, svm_predicted))
from sklearn.metrics import accuracy_score
print("SVM Accuracy Score : ")
print(accuracy_score(y_test, svm_predicted))
print("SVM Recall : ")
print(recall_score(y_test, svm_predicted))
print("SVM Precision : ")
print(precision_score(y_test, svm_predicted))

SVM F1 Score : 
0.27848101265822783
SVM Accuracy Score : 
0.9458174904942965
SVM Recall : 
0.2222222222222222
SVM Precision : 
0.3728813559322034


In [44]:
sgd_grid = GridSearchCV(
        estimator=SGDClassifier(),
        param_grid=[
            {'alpha': [0.00001], 'l1_ratio': [0.15, 0.20, 0.4, 0.6, 0.8] },
            {'alpha': [0.0001], 'l1_ratio': [0.15, 0.20, 0.4, 0.6, 0.8] },
            {'alpha': [0.001], 'l1_ratio': [0.15, 0.20, 0.4, 0.6, 0.8] },
            {'alpha': [0.01], 'l1_ratio': [0.15, 0.20, 0.4, 0.6, 0.8] },
            
        ],
        cv=10, scoring='recall', verbose=1, n_jobs=-1)

grid_result = sgd_grid.fit(train_tfidf, y_train)

best_params = grid_result.best_params_

best_sgd = SGDClassifier(alpha=best_params["alpha"], l1_ratio=best_params["l1_ratio"])
best_sgd.fit(train_tfidf, y_train)

sgd_predicted = best_sgd.predict(test_tfidf)

Fitting 10 folds for each of 20 candidates, totalling 200 fits


/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

...

/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
/home/user/anaconda3

In [45]:
grid_result.best_params_

{'alpha': 1e-05, 'l1_ratio': 0.2}

In [46]:
print("SGD F1 Score : ")
print(f1_score(y_test, sgd_predicted))
from sklearn.metrics import accuracy_score
print("SGD Accuracy Score : ")
print(accuracy_score(y_test, sgd_predicted))
print("SGD Recall : ")
print(recall_score(y_test, sgd_predicted))
print("SGD Precision : ")
print(precision_score(y_test, sgd_predicted))

SGD F1 Score : 
0.0
SGD Accuracy Score : 
0.9529467680608364
SGD Recall : 
0.0
SGD Precision : 
0.0


/home/user/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)


In [31]:
"""from sklearn.linear_model import SGDClassifier
sgd = SGDClassifier()
sgd.fit(train_tfidf, y_train)
sgd_predicted = sgd.predict(test_tfidf)
print("SGD F1 Score : ")
print(f1_score(y_test, sgd_predicted))
from sklearn.metrics import accuracy_score
print("SGD Accuracy Score : ")
print(accuracy_score(y_test, sgd_predicted))
print("SGD Recall : ")
print(recall_score(y_test, sgd_predicted))
print("SGD Precision : ")
print(precision_score(y_test, sgd_predicted))"""

'from sklearn.linear_model import SGDClassifier\nsgd = SGDClassifier()\nsgd.fit(train_tfidf, y_train)\nsgd_predicted = sgd.predict(test_tfidf)\nprint("SGD F1 Score : ")\nprint(f1_score(y_test, sgd_predicted))\nfrom sklearn.metrics import accuracy_score\nprint("SGD Accuracy Score : ")\nprint(accuracy_score(y_test, sgd_predicted))\nprint("SGD Recall : ")\nprint(recall_score(y_test, sgd_predicted))\nprint("SGD Precision : ")\nprint(precision_score(y_test, sgd_predicted))'

In [32]:
print("SGD F1 Score : ")
print(f1_score(y_test, sgd_predicted))
from sklearn.metrics import accuracy_score
print("SGD Accuracy Score : ")
print(accuracy_score(y_test, sgd_predicted))
print("SGD Recall : ")
print(recall_score(y_test, sgd_predicted))
print("SGD Precision : ")
print(precision_score(y_test, sgd_predicted))

SGD F1 Score : 
0.12068965517241381
SGD Accuracy Score : 
0.9515209125475285
SGD Recall : 
0.06862745098039216
SGD Precision : 
0.5


In [33]:
score = cross_val_score(sgd,  train_tfidf, y_train, cv=5, scoring="f1_macro")
print("Cross-val SGD score : " + str(score))
print("Cross-val SGD score mean: " + str(score.mean()))
print("Cross-val SGD score standart deviation : " + str(score.std()))

NameError: name 'sgd' is not defined

In [38]:
from sklearn.ensemble import RandomForestClassifier

In [39]:
rf_grid = GridSearchCV(
        estimator=RandomForestClassifier(),
        param_grid={
            'n_estimators': [10, 20, 50, 100]
            
        },
        cv=10, scoring='recall', verbose=1, n_jobs=-1)

grid_result = rf_grid.fit(train_tfidf, y_train)

best_params = grid_result.best_params_

best_rf = RandomForestClassifier(n_estimators=best_params['n_estimators'])
best_rf.fit(train_tfidf, y_train)

rf_predicted = best_rf.predict(test_tfidf)

Fitting 10 folds for each of 4 candidates, totalling 40 fits


[Parallel(n_jobs=-1)]: Done  40 out of  40 | elapsed:   39.0s finished


In [40]:
print("RF F1 Score : ")
print(f1_score(y_test, rf_predicted))
from sklearn.metrics import accuracy_score
print("RF Accuracy Score : ")
print(accuracy_score(y_test, rf_predicted))
print("RF Recall : ")
print(recall_score(y_test, rf_predicted))
print("RF Precision : ")
print(precision_score(y_test, rf_predicted))

RF F1 Score : 
0.0
RF Accuracy Score : 
0.9560570071258907
RF Recall : 
0.0
RF Precision : 
0.0


/home/user/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/user/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)


In [41]:
"""lr = RandomForestClassifier(random_state=0)
lr.fit(train_tfidf, y_train)
lr_predicted = lr.predict(test_tfidf)
print("SGD F1 Score : ")
print(f1_score(y_test, lr_predicted))
from sklearn.metrics import accuracy_score
print("SGD Accuracy Score : ")
print(accuracy_score(y_test, lr_predicted))
print("SGD Recall : ")
print(recall_score(y_test, lr_predicted))
print("SGD Precision : ")
print(precision_score(y_test, lr_predicted))"""

'lr = RandomForestClassifier(random_state=0)\nlr.fit(train_tfidf, y_train)\nlr_predicted = lr.predict(test_tfidf)\nprint("SGD F1 Score : ")\nprint(f1_score(y_test, lr_predicted))\nfrom sklearn.metrics import accuracy_score\nprint("SGD Accuracy Score : ")\nprint(accuracy_score(y_test, lr_predicted))\nprint("SGD Recall : ")\nprint(recall_score(y_test, lr_predicted))\nprint("SGD Precision : ")\nprint(precision_score(y_test, lr_predicted))'

In [42]:
prediction_df = pd.DataFrame(columns=["svm", "sgd", "rf", "result"])

prediction_df['svm'] = svm_predicted
prediction_df['sgd'] = sgd_predicted
prediction_df['rf'] = rf_predicted


for idx, elem in prediction_df.iterrows():
    count = 0
    if elem['svm'] == 1:
        count = count + 1
    if elem['sgd'] == 1:
        count = count + 1
    if elem['rf'] == 1:
        count = count + 1
    if count >= 2:
        prediction_df['result'].values[idx] = 1
    else:
        prediction_df['result'].values[idx] = 0
        
print("Result F1 Score : ")
print(f1_score(y_test, prediction_df['result'].tolist(), average="macro"))
from sklearn.metrics import accuracy_score
print("Result Accuracy Score : ")
print(accuracy_score(y_test, prediction_df['result'].tolist()))
print("Result Recall : ")
print(recall_score(y_test, prediction_df['result'].tolist()))
print("Result Precision : ")
print(precision_score(y_test, prediction_df['result'].tolist()))

print(classification_report(y_test, prediction_df['result'].tolist(), target_names=['class 0', 'class 1']))

Result F1 Score : 
0.6426697530864198
Result Accuracy Score : 
0.9477434679334917
Result Recall : 
0.2702702702702703
Result Precision : 
0.37037037037037035
             precision    recall  f1-score   support

    class 0       0.97      0.98      0.97       805
    class 1       0.37      0.27      0.31        37

avg / total       0.94      0.95      0.94       842



In [36]:
prediction_df

svm  sgd   rf result
0     0.0  0.0  0.0      0
1     1.0  0.0  1.0      1
2     0.0  0.0  0.0      0
3     0.0  0.0  0.0      0
4     0.0  0.0  0.0      0
5     0.0  0.0  0.0      0
6     0.0  0.0  0.0      0
7     1.0  1.0  1.0      1
8     0.0  0.0  0.0      0
9     0.0  0.0  0.0      0
10    0.0  0.0  0.0      0
11    0.0  0.0  0.0      0
12    0.0  0.0  0.0      0
13    0.0  0.0  0.0      0
14    0.0  0.0  0.0      0
15    0.0  0.0  0.0      0
16    0.0  0.0  0.0      0
17    1.0  0.0  0.0      0
18    1.0  0.0  0.0      0
19    0.0  0.0  0.0      0
20    0.0  0.0  0.0      0
21    0.0  0.0  0.0      0
22    0.0  0.0  1.0      0
23    0.0  0.0  0.0      0
24    0.0  0.0  0.0      0
25    0.0  0.0  0.0      0
26    1.0  1.0  1.0      1
27    0.0  0.0  0.0      0
28    0.0  0.0  0.0      0
29    1.0  1.0  1.0      1
...   ...  ...  ...    ...
1046  0.0  0.0  0.0      0
1047  0.0  0.0  0.0      0
1048  0.0  0.0  0.0      0
1049  0.0  0.0  0.0      0
1050  0.0  0.0  0.0      0
1051  0.0  0.0  0.0      0
1052  1.0  0.0  1.0      1
1053  0.0  0.0  0.0      0
1054  0.0  0.0  1.0      0
1055  1.0  0.0  1.0      1
1056  0.0  0.0  0.0      0
1057  0.0  0.0  0.0      0
1058  0.0  0.0  0.0      0
1059  0.0  0.0  0.0      0
1060  0.0  0.0  0.0      0
1061  0.0  0.0  0.0      0
1062  0.0  0.0  0.0      0
1063  1.0  0.0  0.0      0
1064  0.0  0.0  0.0      0
1065  0.0  0.0  0.0      0
1066  0.0  0.0  0.0      0
1067  0.0  0.0  0.0      0
1068  0.0  0.0  0.0      0
1069  0.0  0.0  0.0      0
1070  0.0  0.0  0.0      0
1071  1.0  1.0  1.0      1
1072  0.0  0.0  0.0      0
1073  0.0  0.0  0.0      0
1074  0.0  0.0  0.0      0
1075  1.0  1.0  1.0      1

[1076 rows x 4 columns]

In [37]:
prediction_df_one = pd.DataFrame(columns=["svm", "sgd", "rf", "result"])
prediction_df_one['svm'] = svm_predicted
prediction_df_one['sgd'] = sgd_predicted
prediction_df_one['rf'] = rf_predicted

for idx, elem in prediction_df_one.iterrows():
    count = 0
    if elem['svm'] == 1:
        count = count + 1
    if elem['sgd'] == 1:
        count = count + 1
    if elem['rf'] == 1:
        count = count + 1
    if count >= 1:
        prediction_df_one['result'].values[idx] = 1
    else:
        prediction_df_one['result'].values[idx] = 0
        
print("Result F1 Score : ")
print(f1_score(y_test, prediction_df_one['result'].tolist(), average="macro"))
from sklearn.metrics import accuracy_score
print("Result Accuracy Score : ")
print(accuracy_score(y_test, prediction_df_one['result'].tolist()))
print("Result Recall : ")
print(recall_score(y_test, prediction_df_one['result'].tolist()))
print("Result Precision : ")
print(precision_score(y_test, prediction_df_one['result'].tolist()))

print(classification_report(y_test, prediction_df_one['result'].tolist(), target_names=['class 0', 'class 1']))

Result F1 Score : 
0.8463790354324142
Result Accuracy Score : 
0.9005576208178439
Result Recall : 
0.8208955223880597
Result Precision : 
0.6991525423728814
             precision    recall  f1-score   support

    class 0       0.96      0.92      0.94       875
    class 1       0.70      0.82      0.76       201

avg / total       0.91      0.90      0.90      1076



In [57]:
prediction_df_three = pd.DataFrame(columns=["svm", "sgd", "rf", "result"])
prediction_df_three['svm'] = svm_predicted
prediction_df_three['sgd'] = sgd_predicted
prediction_df_three['rf'] = rf_predicted

for idx, elem in prediction_df_three.iterrows():
    count = 0
    if elem['svm'] == 1:
        count = count + 1
    if elem['sgd'] == 1:
        count = count + 1
    if elem['rf'] == 1:
        count = count + 1
    if count >= 3:
        prediction_df_three['result'].values[idx] = 1
    else:
        prediction_df_three['result'].values[idx] = 0
        
print("Result F1 Score : ")
print(f1_score(y_test, prediction_df_three['result'].tolist(), average="macro"))
from sklearn.metrics import accuracy_score
print("Result Accuracy Score : ")
print(accuracy_score(y_test, prediction_df_three['result'].tolist()))
print("Result Recall : ")
print(recall_score(y_test, prediction_df_three['result'].tolist()))
print("Result Precision : ")
print(precision_score(y_test, prediction_df_three['result'].tolist()))

print(classification_report(y_test, prediction_df_three['result'].tolist(), target_names=['class 0', 'class 1']))

Result F1 Score : 
0.8810065651550258
Result Accuracy Score : 
0.9025210084033614
Result Recall : 
0.7553191489361702
Result Precision : 
0.922077922077922
             precision    recall  f1-score   support

    class 0       0.90      0.97      0.93       407
    class 1       0.92      0.76      0.83       188

avg / total       0.90      0.90      0.90       595



In [60]:
prediction_df_three['y_test'] = y_test.values
prediction_df_three['X_test'] = X_test.values

In [68]:
prediction_df_three.loc[(prediction_df_three.result == 1) & (prediction_df_three.y_test == 0)]

svm  sgd   rf result  y_test  \
38   1.0  1.0  1.0      1     0.0   
61   1.0  1.0  1.0      1     0.0   
113  1.0  1.0  1.0      1     0.0   
193  1.0  1.0  1.0      1     0.0   
245  1.0  1.0  1.0      1     0.0   
259  1.0  1.0  1.0      1     0.0   
295  1.0  1.0  1.0      1     0.0   
358  1.0  1.0  1.0      1     0.0   
391  1.0  1.0  1.0      1     0.0   
448  1.0  1.0  1.0      1     0.0   
450  1.0  1.0  1.0      1     0.0   
476  1.0  1.0  1.0      1     0.0   

                                                X_test  
38   Patten hopes Tiananmen crackdown remains on sy...  
61   HK sets "national security" limits on protests...  
113  Hong Kong civil liberties amendments to go to ...  
193  China blasts Japan over islands dispute.\nChin...  
245  HK future leader Tung pledges to protect right...  
259  Britain to protest China plans for Hong Kong l...  
295  Trial of China dissident Wang to start Wednesd...  
358  China region in call to battle unrest, religio...  
391  HK blasts China for leaking PLA recce party de...  
448  China policewoman kills kindergarten kidnapper...  
450  China police clear Tiananmen Square.\nUnarmed ...  
476  No accord with China to shelve isles dispute-J...

In [70]:
prediction_df_three.iloc[61].X_test

'HK sets "national security" limits on protests.\nHong Kong, recently unified with China, handed police wide discretionary powers on Friday to ban protests or political groups on "national security" grounds.\nThe government issued guidelines defining "national security" and allowing the chief of police to ban gatherings if they threaten China\'s "national security", promote independence for Tibet or Taiwan, or cause public disturbance.\nPolice can also ask the government\'s security chief to cancel the registration of a society due to national security.\nThe guidelines expand on laws enacted by Hong Kong\'s China-appointed legislature hours after Britain handed over this former colony of 156 years back to China on July 1.\nThe laws, pushed through by Hong Kong\'s new leader Tung Chee-hwa at China\'s behest, set curbs on protests and the registration of parties and included the concept of "national security". The concept was not defined at the time.\nThe latest development came hard on 

In [33]:
df_all = pd.DataFrame()

In [34]:
df_all['sentence'] = X_test
df_all['label'] = y_test

In [35]:
df_all = df_all.loc[df_all.label == 1]

In [36]:
X_test = df_all['sentence']
y_test = df_all['label']

In [37]:
from sklearn.feature_extraction.text import TfidfVectorizer

tfidf_vect = TfidfVectorizer(stop_words='english', ngram_range=(1,2), tokenizer=dummy_fun, preprocessor=dummy_fun, analyzer='word', token_pattern=r'\w{1,}', max_features=20000)
train_tfidf = tfidf_vect.fit_transform(X_train)
test_tfidf = tfidf_vect.transform(X_test)

In [40]:
ones_predict_sgd = sgd.predict(test_tfidf)
ones_predict_svm = best_svr.predict(test_tfidf)
ones_predict_lr = lr.predict(test_tfidf)

In [41]:
print(accuracy_score(y_test, ones_predict_sgd))
print(accuracy_score(y_test, ones_predict_svm))
print(accuracy_score(y_test, ones_predict_lr))

0.8285714285714286
0.84
0.7828571428571428


In [42]:
len(df_all)

175

In [43]:
y_test

1578    1.0
1279    1.0
850     1.0
2767    1.0
1368    1.0
1435    1.0
1499    1.0
1248    1.0
1156    1.0
552     1.0
1251    1.0
1195    1.0
1891    1.0
1706    1.0
1836    1.0
944     1.0
1696    1.0
1171    1.0
1914    1.0
1286    1.0
1442    1.0
1460    1.0
875     1.0
832     1.0
1803    1.0
1332    1.0
1172    1.0
1237    1.0
1472    1.0
1179    1.0
       ... 
1441    1.0
962     1.0
1131    1.0
1370    1.0
150     1.0
961     1.0
1548    1.0
1223    1.0
1551    1.0
1620    1.0
1244    1.0
1265    1.0
1149    1.0
1047    1.0
1959    1.0
1614    1.0
1947    1.0
1042    1.0
1452    1.0
1457    1.0
811     1.0
1582    1.0
1540    1.0
1606    1.0
890     1.0
495     1.0
1713    1.0
1788    1.0
1599    1.0
1839    1.0
Name: label, Length: 175, dtype: float64

In [44]:
from sklearn.metrics import classification_report

In [45]:
print(classification_report(y_test, ones_predict_sgd, target_names=["class 0", "class 1"]))

             precision    recall  f1-score   support

    class 0       0.00      0.00      0.00         0
    class 1       1.00      0.83      0.91       175

avg / total       1.00      0.83      0.91       175



/home/user/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)


In [46]:
print(classification_report(y_test, ones_predict_svm, target_names=["class 0", "class 1"]))

             precision    recall  f1-score   support

    class 0       0.00      0.00      0.00         0
    class 1       1.00      0.84      0.91       175

avg / total       1.00      0.84      0.91       175



/home/user/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)


In [47]:
print(classification_report(y_test, ones_predict_lr, target_names=["class 0", "class 1"]))

             precision    recall  f1-score   support

    class 0       0.00      0.00      0.00         0
    class 1       1.00      0.78      0.88       175

avg / total       1.00      0.78      0.88       175



/home/user/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)


In [48]:
len(df)

2971

In [49]:
df.to_excel("all_china.xlsx")

In [139]:
X_test.tolist()

[['Hong',
  'Kong',
  'activist',
  'vow',
  'to',
  'flout',
  'protest',
  'ban.',
  'Hong',
  "Kong's",
  'pro-democracy',
  'activist',
  'on',
  'Thursday',
  'vowed',
  'to',
  'defy',
  'a',
  'Beijing',
  'warning',
  'that',
  'rally',
  'marking',
  'the',
  'crushing',
  'of',
  'protest',
  'at',
  'Tiananmen',
  'Square',
  'would',
  'not',
  'be',
  'tolerated',
  'after',
  'the',
  'handover',
  'to',
  'China.',
  'More',
  'than',
  'year',
  'of',
  'colonial',
  'rule',
  'end',
  'when',
  'Hong',
  'Kong',
  'reverts',
  'to',
  'China',
  'next',
  'July',
  'under',
  'a',
  'Sino-British',
  'Joint',
  'Declaration',
  'that',
  'pledge',
  'the',
  'territory',
  'considerable',
  'autonomy',
  'and',
  'the',
  'right',
  'to',
  'maintain',
  'capitalist',
  'freedom',
  'for',
  'years.',
  'Chinese',
  'Foreign',
  'Minister',
  'Qian',
  'Qichen',
  'told',
  'the',
  'Asian',
  'Wall',
  'Street',
  'Journal',
  'on',
  'Wednesday',
  'that',
  'Hong',


In [74]:
X_test.to_excel('/home/user/Desktop/china_document_level/data/X_test_China.xlsx')
X_train.to_excel('/home/user/Desktop/china_document_level/data/X_train_China.xlsx')

In [77]:
len(X_train)

2377